# IBM Applied Data Science Capstone – Coursera
Opening a new Coffee shop in New York, USA
New investor is looking to start a new Coffee Shop in New York, USA neighborhoods

.Build a dataframe of neighborhoods of New York, USA by web scraping the data from Wikipedia page
.Get the geographical coordinates of the neighborhoods
.Obtain the venue data for the neighborhoods from Foursquare API
.Explore and cluster the neighborhoods
.Select the best cluster to open a new Coffee Shop


### Introduction
New York City is one of the most famous, romanticized and desired cities for living in the world due to its image portrayed in the pop culture. Some of the worlds' most popular content creators and influencers are located in the city for its stunning backgrounds and instagrammable dining and coffee locations. Combining that with the overall growing trend for coffee and small business coffee shops makes it an attractive investment to open a new coffee shop specifically in NYC where this coffee shop is likely to receive a lot of attention on social media to drive revenue.

Based on the business type and for the sake of this capstone project, our simplified assumptions for the best location would be a high-density population area with a relatively low number of existing coffee shops. Existing competition might in reality be a good factor as a specific neighborhood could be famous for its coffee shops and would attract more customers. In this project, we will examine the landscape of the city on existing competition to identify the best location for the investment.



### Data
Data required to approach the above business case should include New York City neighborhoods' and boroughs' geographical locations (latitude, longitude) and boroughs' population density.

New York City data containing the neighborhoods and boroughs latitudes and longitudes can be obtained from  https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json. While FourSquare API will be used to obtain data on existing coffee shops.



### Methodology
After collecting the data, it will be wrangled into a dataframe format. Using the density data all above average density boroughs will be mapped onto the map. Then using Foursquare we will locate all venues in the following boroughs and then filter by "coffee shop" locations. Finally, the data be will be visually assessed from the resulted map.



### Business Problem
What is the best location(s) for coffee shop in New York City? In what Neighborhood and/or borough is preferred for investing into coffee shop business? What (if any) neighborhood is to go to for a cup of coffee?

###  Import libraries

In [10]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import matplotlib.colors as colors
%matplotlib inline
#!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library


print('Libraries imported.')

Libraries imported.


###  Scrap data from IBM into a DataFrame

In [11]:
!wget -q -O 'newyork_data.json' https://cf-courses-data.s3.us.cloud-object-storage.appdomain.cloud/IBMDeveloperSkillsNetwork-DS0701EN-SkillsNetwork/labs/newyork_data.json
print('Data downloaded!')

Data downloaded!


In [12]:
with open('newyork_data.json') as json_data:
    newyork_data = json.load(json_data)

In [13]:
newyork_data['features'][0]

{'type': 'Feature',
 'id': 'nyu_2451_34572.1',
 'geometry': {'type': 'Point',
  'coordinates': [-73.84720052054902, 40.89470517661]},
 'geometry_name': 'geom',
 'properties': {'name': 'Wakefield',
  'stacked': 1,
  'annoline1': 'Wakefield',
  'annoline2': None,
  'annoline3': None,
  'annoangle': 0.0,
  'borough': 'Bronx',
  'bbox': [-73.84720052054902,
   40.89470517661,
   -73.84720052054902,
   40.89470517661]}}

In [14]:
columns_name=['Borough', 'Neighborhood', 'Latitude', 'Longitude']
neighborhoods = pd.DataFrame(columns=columns_name)

In [15]:
neighborhoods_data=newyork_data['features']
for data in neighborhoods_data:
    borough = neighborhood_name = data['properties']['borough'] 
    neighborhood_name = data['properties']['name']
        
    neighborhood_latlon = data['geometry']['coordinates']
    neighborhood_lat = neighborhood_latlon[1]
    neighborhood_lon = neighborhood_latlon[0]
    
    neighborhoods = neighborhoods.append({'Borough': borough,
                                          'Neighborhood': neighborhood_name,
                                          'Latitude': neighborhood_lat,
                                          'Longitude': neighborhood_lon}, ignore_index=True)

In [16]:
neighborhoods.head()

Borough Neighborhood   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [17]:
print("The dataframe has {} boroughs and {} neighborhoods".format( len(neighborhoods['Borough'].unique()),neighborhoods.shape[0]))

The dataframe has 5 boroughs and 306 neighborhoods


In [18]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


In [19]:
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Borough'], neighborhoods['Neighborhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

In [20]:
CLIENT_ID = 'PNSBWFVXYOJKYJPV1JT3MJMILB3PLRLAMYBSBCRMNWNVNZRH' # your Foursquare ID
CLIENT_SECRET = 'JGJHDJR1UALFBCQOZSFBNVLCEW3ZMDCESRRP4W5ACVHLY1NK' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: PNSBWFVXYOJKYJPV1JT3MJMILB3PLRLAMYBSBCRMNWNVNZRH
CLIENT_SECRET:JGJHDJR1UALFBCQOZSFBNVLCEW3ZMDCESRRP4W5ACVHLY1NK


In [21]:
radius = 5000
LIMIT = 100

venues = []

for lat, long, neighborhood in zip(neighborhoods['Latitude'], neighborhoods['Longitude'], neighborhoods['Neighborhood']):
    
    # create the API request URL
    url = "https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}".format(
        CLIENT_ID,
        CLIENT_SECRET,
        VERSION,
        lat,
        long,
        radius, 
        LIMIT)
    
    # make the GET request
    results = requests.get(url).json()["response"]['groups'][0]['items']
    
    # return only relevant information for each nearby venue
    for venue in results:
        venues.append((
            neighborhood,
            lat, 
            long, 
            venue['venue']['name'], 
            venue['venue']['location']['lat'], 
            venue['venue']['location']['lng'],  
            venue['venue']['categories'][0]['name']))

In [120]:
# neighborhood_latitude=40.87655077879964 
# neighborhood_longitude= -73.91065965862981
# venue_id='55f81cd2498ee903149fcc64'
# LIMIT = 100
# radius = 500
# url = 'https://api.foursquare.com/v2/venues/{}?&client_id={}&client_secret={}&v={}'.format(
#         venue_id,
#         CLIENT_ID, 
#         CLIENT_SECRET, 
#         VERSION)
# requests.get(url).json()["response"]
# lat=40.87655077879964 
# lng= -73.91065965862981
# venue_id='55f81cd2498ee903149fcc64'
# LIMIT = 100
# radius = 500
# url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
#         CLIENT_ID, 
#         CLIENT_SECRET, 
#         VERSION, 
#         lat, 
#         lng, 
#         radius, 
#         LIMIT)
# requests.get(url).json()

{'meta': {'code': 200, 'requestId': '611d61f1f7a6451afa2bc05f'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Marble Hill',
  'headerFullLocation': 'Marble Hill, New York',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 23,
  'suggestedBounds': {'ne': {'lat': 40.88105078329964,
    'lng': -73.90471933917806},
   'sw': {'lat': 40.87205077429964, 'lng': -73.91659997808156}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4baf59e8f964a520a6f93be3',
       'name': 'Bikram Yoga',
       'location': {'address': '5500 Broadway',
        'crossStreet': '230th Street',
        'lat': 40.876843690797934,
        'lng': -73.90620384419528,
        'labeledLatLngs': [{'la

In [22]:
# convert the venues list into a new DataFrame
venues_df = pd.DataFrame(venues)

# define the column names
venues_df.columns = ['Neighborhood', 'Latitude', 'Longitude', 'Venue_Name', 'Venue_Latitude', 'Venue_Longitude', 'Venue_Category']

print(venues_df.shape)
venues_df.head()


(30526, 7)


Neighborhood   Latitude  Longitude                   Venue_Name  \
0    Wakefield  40.894705 -73.847201             Lollipops Gelato   
1    Wakefield  40.894705 -73.847201              Ali's Roti Shop   
2    Wakefield  40.894705 -73.847201           Ripe Kitchen & Bar   
3    Wakefield  40.894705 -73.847201     Kingston Tropical Bakery   
4    Wakefield  40.894705 -73.847201  Jackie's West Indian Bakery   

   Venue_Latitude  Venue_Longitude        Venue_Category  
0       40.894123       -73.845892          Dessert Shop  
1       40.894036       -73.856935  Caribbean Restaurant  
2       40.898152       -73.838875  Caribbean Restaurant  
3       40.888568       -73.859885                Bakery  
4       40.889283       -73.843310  Caribbean Restaurant

In [23]:
bb=venues_df[venues_df['Venue_Category']=='Coffee Shop']
cc=bb.groupby(['Neighborhood']).count()
copy=cc.sort_values(ascending=False,by='Venue_Category')
copy

Latitude  Longitude  Venue_Name  Venue_Latitude  \
Neighborhood                                                                 
Sunnyside                         7          7           7               7   
Red Hook                          6          6           6               6   
Bay Terrace                       6          6           6               6   
Ocean Hill                        6          6           6               6   
Hamilton Heights                  6          6           6               6   
Old Town                          6          6           6               6   
Melrose                           6          6           6               6   
Prospect Lefferts Gardens         6          6           6               6   
Bushwick                          6          6           6               6   
New Lots                          6          6           6               6   
Country Club                      6          6           6               6   
Concourse Village                 6          6           6               6   
Prince's Bay                      6          6           6               6   
Gowanus                           6          6           6               6   
Clason Point                      6          6           6               6   
Castle Hill                       5          5           5               5   
Highland Park                     5          5           5               5   
Cypress Hills                     5          5           5               5   
Park Slope                        5          5           5               5   
Brownsville                       5          5           5               5   
Unionport                         5          5           5               5   
Pelham Bay                        5          5           5               5   
Downtown                          5          5           5               5   
East New York                     5          5           5               5   
Boerum Hill                       5          5           5               5   
Sunset Park                       5          5           5               5   
Woodrow                           5          5           5               5   
Mariner's Harbor                  5          5           5               5   
Graniteville                      5          5           5               5   
Erasmus                           5          5           5               5   
Far Rockaway                      5          5           5               5   
East Williamsburg                 4          4           4               4   
Crown Heights                     4          4           4               4   
Fort Greene                       4          4           4               4   
Hunts Point                       4          4           4               4   
Rugby                             4          4           4               4   
Concourse                         4          4           4               4   
Sandy Ground                      4          4           4               4   
Schuylerville                     4          4           4               4   
Stapleton                         4          4           4               4   
Flatlands                         4          4           4               4   
Great Kills                       4          4           4               4   
Ditmas Park                       4          4           4               4   
Port Richmond                     4          4           4               4   
Prospect Heights                  4          4           4               4   
Emerson Hill                      4          4           4               4   
Richmond Town                     4          4           4               4   
Elm Park                          4          4           4               4   
Egbertville                       4          4           4               4   
St. George                        4          4   

In [24]:
copy.groupby(["Neighborhood"]).count()


Latitude  Longitude  Venue_Name  Venue_Latitude  \
Neighborhood                                                                 
Allerton                          1          1           1               1   
Annadale                          1          1           1               1   
Arden Heights                     1          1           1               1   
Arlington                         1          1           1               1   
Arrochar                          1          1           1               1   
Arverne                           1          1           1               1   
Astoria                           1          1           1               1   
Astoria Heights                   1          1           1               1   
Auburndale                        1          1           1               1   
Battery Park City                 1          1           1               1   
Bay Ridge                         1          1           1               1   
Bay Terrace                       1          1           1               1   
Baychester                        1          1           1               1   
Bayside                           1          1           1               1   
Bayswater                         1          1           1               1   
Bedford Park                      1          1           1               1   
Bedford Stuyvesant                1          1           1               1   
Beechhurst                        1          1           1               1   
Bellaire                          1          1           1               1   
Belle Harbor                      1          1           1               1   
Bellerose                         1          1           1               1   
Belmont                           1          1           1               1   
Bensonhurst                       1          1           1               1   
Bergen Beach                      1          1           1               1   
Blissville                        1          1           1               1   
Bloomfield                        1          1           1               1   
Boerum Hill                       1          1           1               1   
Borough Park                      1          1           1               1   
Breezy Point                      1          1           1               1   
Briarwood                         1          1           1               1   
Brighton Beach                    1          1           1               1   
Broad Channel                     1          1           1               1   
Broadway Junction                 1          1           1               1   
Bronxdale                         1          1           1               1   
Brooklyn Heights                  1          1           1               1   
Brookville                        1          1           1               1   
Brownsville                       1          1           1               1   
Bulls Head                        1          1           1               1   
Bushwick                          1          1           1               1   
Butler Manor                      1          1           1               1   
Canarsie                          1          1           1               1   
Carnegie Hill                     1          1           1               1   
Carroll Gardens                   1          1           1               1   
Castle Hill                       1          1           1               1   
Castleton Corners                 1          1           1               1   
Central Harlem                    1          1           1               1   
Charleston                        1          1           1               1   
Chelsea                           1          1           1               1   
Chinatown                         1          1           1               1   
City Island                       1          1   

In [25]:

print('There are {} uniques categories.'.format(len(venues_df['Venue_Category'].unique())))

There are 350 uniques categories.


In [26]:
venues_df['Venue_Category'].unique()[:50]

array(['Dessert Shop', 'Caribbean Restaurant', 'Bakery', 'Pub', 'Bar',
       'Pizza Place', 'Pharmacy', 'Trail', 'Café', 'Grocery Store', 'Gym',
       'Bagel Shop', 'Brewery', 'Fast Food Restaurant', 'Ice Cream Shop',
       'Kitchen Supply Store', 'Seafood Restaurant', 'Wine Shop', 'Diner',
       'Brazilian Restaurant', 'Italian Restaurant', 'Pet Store',
       'Furniture / Home Store', 'American Restaurant',
       'Asian Restaurant', 'Sports Bar', 'Burger Joint', 'Park',
       'Donut Shop', 'Deli / Bodega', 'Mexican Restaurant', 'Coffee Shop',
       'Electronics Store', 'Botanical Garden',
       'Cajun / Creole Restaurant', 'Supermarket', 'Spanish Restaurant',
       'Japanese Restaurant', 'Garden', 'Track', 'Frozen Yogurt Shop',
       'Video Game Store', 'Liquor Store', 'Beer Bar', 'Exhibit',
       'Vineyard', 'Gift Shop', 'Breakfast Spot', 'Stables',
       'Cosmetics Shop'], dtype=object)

In [27]:

# one hot encoding
nyc_onehot = pd.get_dummies(venues_df[['Venue_Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
nyc_onehot['Neighborhoods'] = venues_df['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [nyc_onehot.columns[-1]] + list(nyc_onehot.columns[:-1])
nyc_onehot = nyc_onehot[fixed_columns]

print(nyc_onehot.shape)
nyc_onehot.head(10)

(30526, 351)


Neighborhoods  Accessories Store  African Restaurant  Airport Food Court  \
0     Wakefield                  0                   0                   0   
1     Wakefield                  0                   0                   0   
2     Wakefield                  0                   0                   0   
3     Wakefield                  0                   0                   0   
4     Wakefield                  0                   0                   0   
5     Wakefield                  0                   0                   0   
6     Wakefield                  0                   0                   0   
7     Wakefield                  0                   0                   0   
8     Wakefield                  0                   0                   0   
9     Wakefield                  0                   0                   0   

   Airport Lounge  Airport Service  American Restaurant  Amphitheater  \
0               0                0                    0             0   
1               0                0                    0             0   
2               0                0                    0             0   
3               0                0                    0             0   
4               0                0                    0             0   
5               0                0                    0             0   
6               0                0                    0             0   
7               0                0                    0             0   
8               0                0                    0             0   
9               0                0                    0             0   

   Animal Shelter  Aquarium  Arcade  Arepa Restaurant  Argentinian Restaurant  \
0               0         0       0                 0                       0   
1               0         0       0                 0                       0   
2               0         0       0                 0                       0   
3               0         0       0                 0                       0   
4               0         0       0                 0                       0   
5               0         0       0                 0                       0   
6               0         0       0                 0                       0   
7               0         0       0                 0                       0   
8               0         0       0                 0                       0   
9               0         0       0                 0                       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0            0           0                    0                 0   
1            0           0                    0                 0   
2            0           0                    0                 0   
3            0           0                    0                 0   
4            0           0                    0                 0   
5            0           0                    0                 0   
6            0           0                    0                 0   
7            0           0                    0                 0   
8            0           0                    0                 0   
9            0           0                    0                 0   

   Athletics & Sports  Austrian Restaurant  Automotive Shop  BBQ Joint  \
0                   0                    0                0          0   
1                   0                    0                0          0   
2                   0                    0                0          0   
3                   0                    0                0          0   
4                   0                    0                0          0   
5                   0                    0                0          0   
6                   0                    0                0          0   
7                   0                    0                0          0   
8                   0

In [28]:
nyc_grouped = nyc_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(nyc_grouped.shape)
nyc_grouped

(302, 351)


Neighborhoods  Accessories Store  African Restaurant  \
0                     Allerton           0.000000                0.00   
1                     Annadale           0.000000                0.00   
2                Arden Heights           0.000000                0.00   
3                    Arlington           0.010000                0.00   
4                     Arrochar           0.000000                0.00   
5                      Arverne           0.000000                0.00   
6                      Astoria           0.000000                0.00   
7              Astoria Heights           0.000000                0.00   
8                   Auburndale           0.000000                0.00   
9                   Bath Beach           0.000000                0.00   
10           Battery Park City           0.000000                0.00   
11                   Bay Ridge           0.000000                0.00   
12                 Bay Terrace           0.000000                0.00   
13                  Baychester           0.000000                0.00   
14                     Bayside           0.000000                0.00   
15                   Bayswater           0.000000                0.00   
16                Bedford Park           0.000000                0.00   
17          Bedford Stuyvesant           0.000000                0.00   
18                  Beechhurst           0.000000                0.00   
19                    Bellaire           0.000000                0.00   
20                Belle Harbor           0.000000                0.00   
21                   Bellerose           0.000000                0.00   
22                     Belmont           0.000000                0.00   
23                 Bensonhurst           0.000000                0.00   
24                Bergen Beach           0.000000                0.00   
25                  Blissville           0.000000                0.00   
26                  Bloomfield           0.000000                0.00   
27                 Boerum Hill           0.000000                0.00   
28                Borough Park           0.000000                0.00   
29                Breezy Point           0.000000                0.00   
30                   Briarwood           0.000000                0.00   
31              Brighton Beach           0.000000                0.00   
32               Broad Channel           0.010309                0.00   
33           Broadway Junction           0.000000                0.00   
34                   Bronxdale           0.000000                0.00   
35            Brooklyn Heights           0.000000                0.00   
36                  Brookville           0.000000                0.00   
37                 Brownsville           0.000000                0.01   
38                  Bulls Head           0.000000                0.00   
39                    Bushwick           0.000000                0.00   
40                Butler Manor           0.000000                0.00   
41             Cambria Heights           0.000000                0.00   
42                    Canarsie           0.000000                0.00   
43               Carnegie Hill           0.000000                0.00   
44             Carroll Gardens           0.000000                0.00   
45                 Castle Hill           0.000000                0.00   
46           Castleton Corners           0.000000                0.00   
47              Central Harlem           0.000000                0.00   
48                  Charleston           0.000000                0.00   
49                     Chelsea           0.000000                0.00   
50                   Chinatown           0.000000                0.00   
51                 City Island           0.000000                0.00   
52                   City Line           0.000000                0.00   
53                Civic Center           0.000000                0.00   
54

In [29]:

len(nyc_grouped[nyc_grouped["Coffee Shop"] > 0])

273

In [30]:
nyc_coffeeshop = nyc_grouped[["Neighborhoods","Coffee Shop"]]
nyc_coffeeshop.head()

Neighborhoods  Coffee Shop
0       Allerton     0.030000
1       Annadale     0.010309
2  Arden Heights     0.010000
3      Arlington     0.030000
4       Arrochar     0.020000

In [31]:
nyc_coffeeshop=nyc_coffeeshop.sort_values(ascending=False,by='Coffee Shop')
nyc_coffeeshop.head()

Neighborhoods  Coffee Shop
55        Clason Point         0.06
202           Old Town         0.06
124   Hamilton Heights         0.06
67        Country Club         0.06
64   Concourse Village         0.06

### Cluster Neighborhoods
Run k-means to cluster the neighborhoods in NYC into 3 clusters.

In [32]:

# set number of clusters
kclusters = 3

nyc_clustering = nyc_coffeeshop.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(nyc_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:30]

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1], dtype=int32)

In [33]:
# Create a new dataframe that includes the cluster label
nyc_merged = nyc_coffeeshop.copy()

# add clustering labels
nyc_merged["Cluster Labels"] = kmeans.labels_


nyc_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
nyc_merged.head(10)

Neighborhood  Coffee Shop  Cluster Labels
55        Clason Point         0.06               1
202           Old Town         0.06               1
124   Hamilton Heights         0.06               1
67        Country Club         0.06               1
64   Concourse Village         0.06               1
171            Melrose         0.06               1
39            Bushwick         0.06               1
191           New Lots         0.06               1
200         Ocean Hill         0.06               1
113            Gowanus         0.06               1

In [34]:
# nyc_merged = nyc_merged.join(neighborhoods.set_index("Neighborhood"), on="Neighborhood")

print(nyc_merged.shape)
nyc_merged # check the last columns!

(306, 6)


Neighborhood  Coffee Shop  Cluster Labels        Borough  \
55                Clason Point     0.060000               1          Bronx   
202                   Old Town     0.060000               1  Staten Island   
124           Hamilton Heights     0.060000               1      Manhattan   
67                Country Club     0.060000               1          Bronx   
64           Concourse Village     0.060000               1          Bronx   
171                    Melrose     0.060000               1          Bronx   
39                    Bushwick     0.060000               1       Brooklyn   
191                   New Lots     0.060000               1       Brooklyn   
200                 Ocean Hill     0.060000               1       Brooklyn   
113                    Gowanus     0.060000               1       Brooklyn   
217               Prince's Bay     0.060000               1  Staten Island   
226                   Red Hook     0.060000               1       Brooklyn   
219  Prospect Lefferts Gardens     0.060000               1       Brooklyn   
299                    Woodrow     0.050000               1  Staten Island   
37                 Brownsville     0.050000               1       Brooklyn   
79               East New York     0.050000               1       Brooklyn   
276                  Unionport     0.050000               1          Bronx   
73                    Downtown     0.050000               1       Brooklyn   
45                 Castle Hill     0.050000               1          Bronx   
69               Cypress Hills     0.050000               1       Brooklyn   
27                 Boerum Hill     0.050000               1       Brooklyn   
92                     Erasmus     0.050000               1       Brooklyn   
93                Far Rockaway     0.050000               1         Queens   
266                Sunset Park     0.050000               1       Brooklyn   
128              Highland Park     0.050000               1       Brooklyn   
207                 Park Slope     0.050000               1       Brooklyn   
209                 Pelham Bay     0.050000               1          Bronx   
169           Mariner's Harbor     0.050000               1  Staten Island   
115               Graniteville     0.050000               1  Staten Island   
220        Prospect Park South     0.040000               1       Brooklyn   
242                      Rugby     0.040000               1       Brooklyn   
161                      Malba     0.040000               1         Queens   
68               Crown Heights     0.040000               1       Brooklyn   
63                   Concourse     0.040000               1          Bronx   
70                 Ditmas Park     0.040000               1       Brooklyn   
243               Sandy Ground     0.040000               1  Staten Island   
212            Pleasant Plains     0.040000               1  Staten Island   
244              Schuylerville     0.040000               1          Bronx   
156                Little Neck     0.040000               1         Queens   
228             Remsen Village     0.040000               1       Brooklyn   
77               East Flatbush     0.040000               1       Brooklyn   
152            Lighthouse Hill     0.040000               1  Staten Island   
172             Middle Village     0.040000               1         Queens   
251                  Soundview     0.040000               1          Bronx   
87                 Egbertville     0.040000               1  Staten Island   
88                    Elm Park     0.040000               1  Staten Island   
138                Hunts Point     0.040000               1          Bronx   
91                Emerson Hill     0.040000               1  Staten Island   
259                 St. George     0.040000               1  Staten Island   
260                  Stapleton     0.040000               1  Staten Island   
270              Tompkinsville     0.040

In [35]:

# Sort the results by Cluster Labels
print(nyc_merged.shape)
nyc_merged.sort_values(["Cluster Labels"], inplace=True)
nyc_merged

(306, 6)


Neighborhood  Coffee Shop  Cluster Labels        Borough  \
118                  Gravesend     0.000000               0       Brooklyn   
133               Howard Beach     0.010000               0         Queens   
131                 Holliswood     0.010000               0         Queens   
130                     Hollis     0.010000               0         Queens   
129                  Hillcrest     0.010000               0         Queens   
42                    Canarsie     0.010000               0       Brooklyn   
222            Queensboro Hill     0.010000               0         Queens   
49                     Chelsea     0.010000               0      Manhattan   
49                     Chelsea     0.010000               0  Staten Island   
110            Gerritsen Beach     0.010000               0       Brooklyn   
31              Brighton Beach     0.010000               0       Brooklyn   
50                   Chinatown     0.010000               0      Manhattan   
102               Forest Hills     0.010000               0         Queens   
53                Civic Center     0.010000               0      Manhattan   
95          Financial District     0.010000               0      Manhattan   
89                    Elmhurst     0.010000               0         Queens   
83                 Eastchester     0.010000               0          Bronx   
61               College Point     0.010000               0         Queens   
81                East Village     0.010000               0      Manhattan   
66                      Corona     0.010000               0         Queens   
142            Jamaica Estates     0.010000               0         Queens   
108               Fulton Ferry     0.010000               0       Brooklyn   
137              Hunters Point     0.010000               0         Queens   
30                   Briarwood     0.010000               0         Queens   
141             Jamaica Center     0.010000               0         Queens   
1                     Annadale     0.010309               0  Staten Island   
279            Upper West Side     0.010000               0      Manhattan   
283                  Wakefield     0.010000               0          Bronx   
300                   Woodside     0.010000               0         Queens   
227                  Rego Park     0.010000               0         Queens   
229              Richmond Hill     0.010000               0         Queens   
265          Sunnyside Gardens     0.010000               0         Queens   
225                 Ravenswood     0.010000               0         Queens   
273                    Tribeca     0.010000               0      Manhattan   
263            Stuyvesant Town     0.010000               0      Manhattan   
249                       Soho     0.010000               0      Manhattan   
246             Sheepshead Bay     0.010000               0       Brooklyn   
256        Springfield Gardens     0.010000               0         Queens   
234                   Rochdale     0.010000               0         Queens   
280                     Utopia     0.010000               0         Queens   
292             Williamsbridge     0.010000               0          Bronx   
258                 St. Albans     0.010000               0         Queens   
278            Upper East Side     0.010000               0      Manhattan   
151                 Lenox Hill     0.010000               0      Manhattan   
301                  Yorkville     0.010000               0      Manhattan   
143              Jamaica Hills     0.010000               0         Queens   
145                Kew Gardens     0.010000               0         Queens   
163          Manhattan Terrace     0.010000               0       Brooklyn   
213                    Pomonok     0.010000               0         Queens   
198            Oakland Gardens     0.010000               0         Queens   
223               Queensbridge     0.000

In [36]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(nyc_merged['Latitude'], nyc_merged['Longitude'], nyc_merged['Neighborhood'], nyc_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [37]:
map_clusters.save('NYC_neighborhood_map_clusters.html')

### Examine Clusters

In [38]:
k_0=nyc_merged.loc[nyc_merged['Cluster Labels'] == 0].reset_index()
k_0

index         Neighborhood  Coffee Shop  Cluster Labels        Borough  \
0     118            Gravesend     0.000000               0       Brooklyn   
1     133         Howard Beach     0.010000               0         Queens   
2     131           Holliswood     0.010000               0         Queens   
3     130               Hollis     0.010000               0         Queens   
4     129            Hillcrest     0.010000               0         Queens   
5      42             Canarsie     0.010000               0       Brooklyn   
6     222      Queensboro Hill     0.010000               0         Queens   
7      49              Chelsea     0.010000               0      Manhattan   
8      49              Chelsea     0.010000               0  Staten Island   
9     110      Gerritsen Beach     0.010000               0       Brooklyn   
10     31       Brighton Beach     0.010000               0       Brooklyn   
11     50            Chinatown     0.010000               0      Manhattan   
12    102         Forest Hills     0.010000               0         Queens   
13     53         Civic Center     0.010000               0      Manhattan   
14     95   Financial District     0.010000               0      Manhattan   
15     89             Elmhurst     0.010000               0         Queens   
16     83          Eastchester     0.010000               0          Bronx   
17     61        College Point     0.010000               0         Queens   
18     81         East Village     0.010000               0      Manhattan   
19     66               Corona     0.010000               0         Queens   
20    142      Jamaica Estates     0.010000               0         Queens   
21    108         Fulton Ferry     0.010000               0       Brooklyn   
22    137        Hunters Point     0.010000               0         Queens   
23     30            Briarwood     0.010000               0         Queens   
24    141       Jamaica Center     0.010000               0         Queens   
25      1             Annadale     0.010309               0  Staten Island   
26    279      Upper West Side     0.010000               0      Manhattan   
27    283            Wakefield     0.010000               0          Bronx   
28    300             Woodside     0.010000               0         Queens   
29    227            Rego Park     0.010000               0         Queens   
30    229        Richmond Hill     0.010000               0         Queens   
31    265    Sunnyside Gardens     0.010000               0         Queens   
32    225           Ravenswood     0.010000               0         Queens   
33    273              Tribeca     0.010000               0      Manhattan   
34    263      Stuyvesant Town     0.010000               0      Manhattan   
35    249                 Soho     0.010000               0      Manhattan   
36    246       Sheepshead Bay     0.010000               0       Brooklyn   
37    256  Springfield Gardens     0.010000               0         Queens   
38    234             Rochdale     0.010000               0         Queens   
39    280               Utopia     0.010000               0         Queens   
40    292       Williamsbridge     0.010000               0          Bronx   
41    258           St. Albans     0.010000               0         Queens   
42    278      Upper East Side     0.010000               0      Manhattan   
43    151           Lenox Hill     0.010000               0      Manhattan   
44    301            Yorkville     0.010000               0      Manhattan   
45    143        Jamaica Hills     0.010000               0         Queens   
46    145          Kew Gardens     0.010000               0         Queens   
47    163    Manhattan Terrace     0.010000               0       Brooklyn   
48    213              Pomonok     0.010000               0         Queens   
49    198      Oakland Gardens     0.010000               0         Queens   
50    223         Queensbr

In [39]:
k_1=nyc_merged.loc[nyc_merged['Cluster Labels'] == 1]
k_1

Neighborhood  Coffee Shop  Cluster Labels        Borough  \
55                Clason Point         0.06               1          Bronx   
98                   Flatlands         0.04               1       Brooklyn   
60                 Cobble Hill         0.04               1       Brooklyn   
82           East Williamsburg         0.04               1       Brooklyn   
119                Great Kills         0.04               1  Staten Island   
104                Fort Greene         0.04               1       Brooklyn   
127               High  Bridge         0.04               1          Bronx   
270              Tompkinsville         0.04               1  Staten Island   
260                  Stapleton         0.04               1  Staten Island   
259                 St. George         0.04               1  Staten Island   
91                Emerson Hill         0.04               1  Staten Island   
138                Hunts Point         0.04               1          Bronx   
88                    Elm Park         0.04               1  Staten Island   
87                 Egbertville         0.04               1  Staten Island   
172             Middle Village         0.04               1         Queens   
152            Lighthouse Hill         0.04               1  Staten Island   
77               East Flatbush         0.04               1       Brooklyn   
287                 West Farms         0.04               1          Bronx   
228             Remsen Village         0.04               1       Brooklyn   
18                  Beechhurst         0.04               1         Queens   
28                Borough Park         0.04               1       Brooklyn   
15                   Bayswater         0.04               1         Queens   
181                Morris Park         0.04               1          Bronx   
238                   Rosebank         0.04               1  Staten Island   
208                Parkchester         0.04               1          Bronx   
46           Castleton Corners         0.04               1  Staten Island   
285                 Weeksville         0.04               1       Brooklyn   
230              Richmond Town         0.04               1  Staten Island   
295            Windsor Terrace         0.04               1       Brooklyn   
289         Westchester Square         0.04               1          Bronx   
216              Port Richmond         0.04               1  Staten Island   
218           Prospect Heights         0.04               1       Brooklyn   
294                Willowbrook         0.04               1  Staten Island   
25                  Blissville         0.04               1         Queens   
33           Broadway Junction         0.04               1       Brooklyn   
199                    Oakwood         0.04               1  Staten Island   
290                Westerleigh         0.04               1  Staten Island   
156                Little Neck         0.04               1         Queens   
251                  Soundview         0.04               1          Bronx   
212            Pleasant Plains         0.04               1  Staten Island   
276                  Unionport         0.05               1          Bronx   
79               East New York         0.05               1       Brooklyn   
244              Schuylerville         0.04               1          Bronx   
299                    Woodrow         0.05               1  Staten Island   
219  Prospect Lefferts Gardens         0.06               1       Brooklyn   
226                   Red Hook         0.06               1       Brooklyn   
217               Prince's Bay         0.06               1  Staten Island   
73                    Downtown         0.05               1       Brooklyn   
113                    Gowanus         0.06               1       Brooklyn   
191                   New Lots         0.06               1       Brooklyn   
39                    Bushwick         0

In [40]:
k_2=nyc_merged.loc[nyc_merged['Cluster Labels'] == 2]
k_2

Neighborhood  Coffee Shop  Cluster Labels        Borough  \
250            Somerville     0.030000               2         Queens   
139                Inwood     0.030000               2      Manhattan   
254      South Ozone Park     0.030000               2         Queens   
236         Rockaway Park     0.030000               2         Queens   
166         Manor Heights     0.030000               2  Staten Island   
80           East Tremont     0.020000               2          Bronx   
176               Midwood     0.030000               2       Brooklyn   
112              Glendale     0.020000               2         Queens   
74                  Dumbo     0.020000               2       Brooklyn   
173         Midland Beach     0.030000               2  Staten Island   
240             Rossville     0.020000               2  Staten Island   
165        Manhattanville     0.030000               2      Manhattan   
197               Norwood     0.030000               2          Bronx   
182            Morrisania     0.030000               2          Bronx   
116            Grant City     0.030000               2  Staten Island   
206             Park Hill     0.030000               2  Staten Island   
210        Pelham Gardens     0.030000               2          Bronx   
203             Olinville     0.030000               2          Bronx   
261         Starrett City     0.030000               2       Brooklyn   
123           Grymes Hill     0.030000               2  Staten Island   
5                 Arverne     0.030612               2         Queens   
32          Broad Channel     0.030928               2         Queens   
125               Hammels     0.031579               2         Queens   
264             Sunnyside     0.035000               2  Staten Island   
264             Sunnyside     0.035000               2         Queens   
239              Rosedale     0.020000               2         Queens   
211        Pelham Parkway     0.030000               2          Bronx   
235        Rockaway Beach     0.030000               2         Queens   
282          Vinegar Hill     0.020000               2       Brooklyn   
170               Maspeth     0.020000               2         Queens   
47         Central Harlem     0.030000               2      Manhattan   
48             Charleston     0.030000               2  Staten Island   
62                Concord     0.030000               2  Staten Island   
286         West Brighton     0.030000               2  Staten Island   
51            City Island     0.030000               2          Bronx   
59             Co-op City     0.030000               2          Bronx   
58           Clinton Hill     0.030000               2       Brooklyn   
22                Belmont     0.030000               2          Bronx   
56                Clifton     0.030000               2  Staten Island   
296               Wingate     0.030000               2       Brooklyn   
44        Carroll Gardens     0.030000               2       Brooklyn   
13             Baychester     0.030000               2          Bronx   
269             Todt Hill     0.030000               2  Staten Island   
105         Fort Hamilton     0.030000               2       Brooklyn   
11              Bay Ridge     0.030000               2       Brooklyn   
106             Fox Hills     0.030000               2  Staten Island   
12            Bay Terrace     0.030000               2         Queens   
12            Bay Terrace     0.030000               2  Staten Island   
99            Floral Park     0.030000               2         Queens   
96               Flatbush     0.030000               2       Brooklyn   
268           Throgs Neck     0.030000               2          Bronx   
3               Arlington     0.030000               2  Staten Island   
8              Auburndale     0.030000               2         Queens   
16           Bedford Park     0.030000               2          Bronx  

In [42]:
len_cluster_0 = len(k_0)
len_cluster_1 = len(k_1)
len_cluster_2 = len(k_2)

print('Total neighborhoods in cluster 0 =', len_cluster_0)
print('Total neighborhoods in cluster 1 =', len_cluster_1)
print('Total neighborhoods in cluster 2 =', len_cluster_2)

Total neighborhoods in cluster 0 = 98
Total neighborhoods in cluster 1 = 76
Total neighborhoods in cluster 2 = 132


# Conclusion

#### Cluster 0: means that the neighborhoods that have 1 Coffee Shop , around 32%


#### Cluster 1: means that the neighborhoods that have 4 or 5 or 6 Coffee Shops , around 25%


#### Cluster 2: means that the neighborhoods that have 2 or 3 Coffee Shops , around 43%

This is showing that new Coffee Shops can be opened in neighborhoods listed in cluster 1 as less competition compared to cluster 0 and 2. Meanwhile, Coffee Shops in cluster 1 are likely suffering from intense competition due to oversupply because cluster 1 is the neighborhoods that have 4,5 or 6 coffee shops. So we can figure out which boroughs have more coffee shops.

### Now we group them by neighborhood to understand which neighborhoods have more coffee shops

In [43]:
print(k_0.groupby(k_0['Borough']).count()['Coffee Shop'])
print(k_1.groupby(k_1['Borough']).count()['Coffee Shop'])
print(k_2.groupby(k_2['Borough']).count()['Coffee Shop'])



Borough
Bronx             7
Brooklyn         13
Manhattan        32
Queens           42
Staten Island     4
Name: Coffee Shop, dtype: int64
Borough
Bronx            16
Brooklyn         30
Manhattan         1
Queens            7
Staten Island    22
Name: Coffee Shop, dtype: int64
Borough
Bronx            29
Brooklyn         27
Manhattan         7
Queens           32
Staten Island    37
Name: Coffee Shop, dtype: int64


So, we concentrate on cluster 1. we know that the Brooklyn and Manhattan are crowded and their density of population are high. So, we can choose these 2 boroughs but as you can see from above, Brooklyn has many coffee shops on 29 neighborhoods so we rather to choose Manhattan because it has 6 coffee shops on just 1 neighborhood(Hamilton Heights) and the other neighborhoods are on cluster 0 or 2.Thus, we choose other neighborhoods except Hamilton Heights.

In [44]:
print(k_1[k_1['Borough']=='Manhattan'])
# print(k_1[k_1['Borough']=='Brooklyn'])

         Neighborhood  Coffee Shop  Cluster Labels    Borough   Latitude  \
124  Hamilton Heights         0.06               1  Manhattan  40.823604   

     Longitude  
124 -73.949688  


Eliminate 'Hamilton Heights'

In [45]:
manhattan_data = neighborhoods[neighborhoods['Borough'] == 'Manhattan'].reset_index(drop=True)
manhattan_boroughs=manhattan_data[(manhattan_data['Neighborhood']!='Hamilton Heights')]
manhattan_boroughs['Neighborhood']

0             Marble Hill
1               Chinatown
2      Washington Heights
3                  Inwood
5          Manhattanville
6          Central Harlem
7             East Harlem
8         Upper East Side
9               Yorkville
10             Lenox Hill
11       Roosevelt Island
12        Upper West Side
13         Lincoln Square
14                Clinton
15                Midtown
16            Murray Hill
17                Chelsea
18      Greenwich Village
19           East Village
20        Lower East Side
21                Tribeca
22           Little Italy
23                   Soho
24           West Village
25       Manhattan Valley
26    Morningside Heights
27               Gramercy
28      Battery Park City
29     Financial District
30          Carnegie Hill
31                   Noho
32           Civic Center
33          Midtown South
34           Sutton Place
35             Turtle Bay
36             Tudor City
37        Stuyvesant Town
38               Flatiron
39          

### For having accurate neighborhoods and less competition we can eliminate the neighborhoods that are on cluster 2(3 or 2 coffee shops on each neighborhood).

In [46]:
print(k_2[k_2['Borough']=='Manhattan'])


            Neighborhood  Coffee Shop  Cluster Labels    Borough   Latitude  \
139               Inwood         0.03               2  Manhattan  40.867684   
165       Manhattanville         0.03               2  Manhattan  40.816934   
47        Central Harlem         0.03               2  Manhattan  40.815976   
284   Washington Heights         0.03               2  Manhattan  40.851903   
167          Marble Hill         0.02               2  Manhattan  40.876551   
179  Morningside Heights         0.03               2  Manhattan  40.808000   
43         Carnegie Hill         0.02               2  Manhattan  40.782683   

     Longitude  
139 -73.921210  
165 -73.957385  
47  -73.943211  
284 -73.936900  
167 -73.910660  
179 -73.963896  
43  -73.953256  


In [71]:
manhattan_places_for_coffee_shops=manhattan_boroughs[(manhattan_boroughs['Neighborhood']!='Manhattanville')&(manhattan_boroughs['Neighborhood']!='Washington Heights')&(manhattan_boroughs['Neighborhood']!='Inwood')&(manhattan_boroughs['Neighborhood']!='Central Harlem')&(manhattan_boroughs['Neighborhood']!='Carnegie Hill')&(manhattan_boroughs['Neighborhood']!='Marble Hill')&(manhattan_boroughs['Neighborhood']!='Morningside Heights')]

manhattan_places_for_coffee_shops=manhattan_places_for_coffee_shops[['Borough','Neighborhood']]
# copy=copy.reset_index()
# copy['Neighborhood']
# final_result = manhattan_places_for_coffee_shops.join(copy.set_index("Neighborhood"), on="Neighborhood")
final_result=final_result[['Borough','Neighborhood','Venue_Category']]
final_result=final_result[final_result['Venue_Category']>=0]
final_result.rename(columns={'Venue_Category':'Number Of Coffee Shops'})

Borough        Neighborhood  Number Of Coffee Shops
1   Manhattan           Chinatown                     1.0
7   Manhattan         East Harlem                     1.0
8   Manhattan     Upper East Side                     1.0
9   Manhattan           Yorkville                     1.0
10  Manhattan          Lenox Hill                     1.0
12  Manhattan     Upper West Side                     1.0
16  Manhattan         Murray Hill                     2.0
17  Manhattan             Chelsea                     2.0
19  Manhattan        East Village                     1.0
20  Manhattan     Lower East Side                     1.0
21  Manhattan             Tribeca                     1.0
22  Manhattan        Little Italy                     1.0
23  Manhattan                Soho                     1.0
25  Manhattan    Manhattan Valley                     1.0
28  Manhattan   Battery Park City                     1.0
29  Manhattan  Financial District                     1.0
32  Manhattan        Civic Center                     1.0
37  Manhattan     Stuyvesant Town                     1.0